In [259]:
import requests
from bs4 import BeautifulSoup
import requests
from pandas.io.json import json_normalize
import os
import numpy as np
import pandas as pd
import json
import geocoder 
from geopy.geocoders import Nominatim
import folium
from folium import plugins
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
print('Libraries imported.')

Libraries imported.


In [260]:
pageUrl = 'https://en.wikipedia.org/wiki/List_of_wards_in_Bangalore'
page = requests.get(pageUrl).text
soup = BeautifulSoup(page, 'html.parser')

In [261]:
column = ['Ward number','Ward','Area']
rem = [2,4]
temp = soup.find('table',class_="wikitable").find('tbody').find_all('tr')
area_list = []
for i in range(len(temp)):
    if i==0:
        continue
    else:
        place = list(filter(lambda a:a!='',temp[i].text.split('\n')))
        place = [place[i] for i in range(len(place)) if i not in rem]
        area_list.append(place)    

In [262]:
hood = pd.DataFrame(area_list,columns=column)
hood = hood.reindex(columns=['Ward number','Area','Ward'])
hood['Latitude'] = ''
hood['Longitude'] = ''
hood.head(10)

Ward number             Area                      Ward Latitude Longitude
0           1        Yelahanka                Kempegowda                   
1           2        Yelahanka              Chowdeshwari                   
2           3        Yelahanka                     Attur                   
3           4        Yelahanka  Yelahanka Satellite Town                   
4           5  Byatarayanapura                    Jakkur                   
5           6  Byatarayanapura               Thanisandra                   
6           7  Byatarayanapura           Byatarayanapura                   
7           8  Byatarayanapura               Kodigehalli                   
8           9  Byatarayanapura            Vidyaranyapura                   
9          10  Byatarayanapura          Doddabommasandra

In [263]:
address = 'Bangalore, India'
location = geocoder.arcgis(address)
latitude,longitude = location.latlng[0],location.latlng[1]
print('The geograpical coordinate of Bangalore are {}, {}.'.format(latitude,
                                                                   longitude))

The geograpical coordinate of Bangalore are 12.966180000000065, 77.58690000000007.


In [264]:
count=0
for i in hood.index:
    if count%10==0:
        print("{} done..".format(count))
    location = geocoder.arcgis('{}, {}, Bangalore, India'.format(hood['Ward'][i],
                                                                 hood['Area'][i]))
    hood.loc[hood['Ward']==hood['Ward'][i],'Latitude'] = location.latlng[0]
    hood.loc[hood['Ward']==hood['Ward'][i],'Longitude'] = location.latlng[1]
    count+=1

0 done..
10 done..
20 done..
30 done..
40 done..
50 done..
60 done..
70 done..
80 done..
90 done..
100 done..
110 done..
120 done..
130 done..
140 done..
150 done..
160 done..
170 done..
180 done..
190 done..


In [268]:
hood = hood.drop_duplicates(['Latitude','Longitude'],keep='first')
hood.reset_index(drop=True,inplace=True)
hood.head(10)

Ward number                 Area                      Ward Latitude  \
0           1            Yelahanka                Kempegowda  13.0993   
1           2            Yelahanka              Chowdeshwari  13.1081   
2           4            Yelahanka  Yelahanka Satellite Town   13.097   
3           5      Byatarayanapura                    Jakkur  12.9519   
4          10      Byatarayanapura          Doddabommasandra  13.0625   
5          11      Byatarayanapura             Kuvempu Nagar  12.9556   
6          12          Dasarahalli               Shettyhalli  13.0422   
7          13          Dasarahalli               Mallasandra  13.0561   
8          14          Dasarahalli               Bagalagunte   13.057   
9          16  Rajarajeshwarinagar                 Jalahalli  12.9318   

  Longitude  
0   77.5926  
1   77.5937  
2   77.5841  
3   77.5445  
4   77.5591  
5   77.5447  
6   77.5151  
7   77.5123  
8   77.5074  
9   77.5267

In [269]:
map_bangalore = folium.Map(location=[latitude, longitude], zoom_start=11)
for lat, lng, borough, neighborhood in zip(hood['Latitude'], hood['Longitude'], hood['Area'], hood['Ward']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_bangalore)  
    
map_bangalore

In [270]:
beng_map = folium.Map(location=[latitude, longitude],zoom_start=11)

fs = plugins.Fullscreen()
beng_map.add_child(fs)

folium.GeoJson('BBMP.GeoJSON').add_to(beng_map)

beng_map

In [271]:
CLIENT_ID = '3KHJVC5U5PAOGTOZXR2Y5KCYDNGLUYOYDMY5LILY2W34MCAO' # your Foursquare ID
CLIENT_SECRET = 'L0O2VAQ2ETKJJPGWJ554DHC3052O2AVWGCTNYXEGFDG10D11' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 3KHJVC5U5PAOGTOZXR2Y5KCYDNGLUYOYDMY5LILY2W34MCAO
CLIENT_SECRET:L0O2VAQ2ETKJJPGWJ554DHC3052O2AVWGCTNYXEGFDG10D11


In [272]:
LIMIT = 100
radius = 500
count = 0
venues_list = []
for num,lat,long,name,bor in zip(hood['Ward number'],hood['Latitude'],hood['Longitude'],
                                  hood['Ward'],hood['Area']):
    

    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    if count%10==0:
        print("{} done".format(count))
    tries=0
    while(1):
        tries+=1
        if tries%20==0:
            print("Try : {}...".format(tries))
        GET = requests.get(url).json()["response"]
        if len(GET)!=0:
            break
    results = GET['groups'][0]['items']
    count+=1
    venues_list.append([(
            num,
            bor,
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

0 done
10 done
20 done
30 done
40 done
50 done
60 done
70 done
80 done
90 done
100 done
110 done
120 done
130 done
140 done


In [273]:
for i in venues_list:
    for j in range(len(i)):
        if i[j][-1]=='Neighborhood':
            i[j] = tuple(list(i[j][:-1]) + ['Community'])

In [279]:
for i in venues_list:
    for j in i:
        if len(j)!=9:
            print(j)

In [280]:
venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
venues.columns = [
                'Ward number',
                'Area',
                'Ward', 
                'Area Latitude', 
                'Area Longitude', 
                'Venue', 
                'Venue Latitude', 
                'Venue Longitude', 
                'Venue Category']
venues.head()

Ward number       Area        Ward  Area Latitude  Area Longitude  \
0           1  Yelahanka  Kempegowda       13.09931        77.55196   
1           1  Yelahanka  Kempegowda       13.09931        77.55196   
2           1  Yelahanka  Kempegowda       13.09931        77.55196   
3           1  Yelahanka  Kempegowda       13.09931        77.55196   
4           1  Yelahanka  Kempegowda       13.09931        77.55196   

                       Venue  Venue Latitude  Venue Longitude  \
0            Cafe Coffee Day       13.099390        77.588282   
1                     Subway       13.099440        77.589355   
2               NES Bus Stop       13.097684        77.591723   
3  Yelahanka Railway Station       13.102922        77.592396   
4                 Polar Bear       13.099411        77.589397   

        Venue Category  
0                 Café  
1  American Restaurant  
2           Smoke Shop  
3        Train Station  
4       Ice Cream Shop

In [281]:
venues.shape

(1201, 9)

In [282]:
print('There are {} uniques categories.'.format(len(venues['Venue Category'].unique())))
venues.groupby(["Ward number","Area", "Ward"]).count()

There are 170 uniques categories.


Area Latitude  \
Ward number Area             Ward                                
1           Yelahanka        Kempegowda                      5   
10          Byatarayanapura  Doddabommasandra                4   
100         Rajajinagar      Basaveshwara Nagar             19   
101         Rajajinagar      Kamakshipalya                   2   
103         Govindarajnagara Kaveripura                      1   
...                                                        ...   
95          Gandhinagar      Subhash Nagar                  15   
96          Gandhinagar      Okalipuram                      1   
97          Rajajinagar      Dayananda Nagar                 6   
98          Rajajinagar      Prakash Nagar                   4   
99          Rajajinagar      Rajaji Nagar                    5   

                                                 Area Longitude  Venue  \
Ward number Area             Ward                                        
1           Yelahanka        Kempegowda                       5      5   
10          Byatarayanapura  Doddabommasandra                 4      4   
100         Rajajinagar      Basaveshwara Nagar              19     19   
101         Rajajinagar      Kamakshipalya                    2      2   
103         Govindarajnagara Kaveripura                       1      1   
...                                                         ...    ...   
95          Gandhinagar      Subhash Nagar                   15     15   
96          Gandhinagar      Okalipuram                       1      1   
97          Rajajinagar      Dayananda Nagar                  6      6   
98          Rajajinagar      Prakash Nagar                    4      4   
99          Rajajinagar      Rajaji Nagar                     5      5   

                                                 Venue Latitude  \
Ward number Area             Ward                                 
1           Yelahanka        Kempegowda                       5   
10          Byatarayanapura  Doddabommasandra                 4   
100         Rajajinagar      Basaveshwara Nagar              19   
101         Rajajinagar      Kamakshipalya                    2   
103         Govindarajnagara Kaveripura                       1   
...                                                         ...   
95          Gandhinagar      Subhash Nagar                   15   
96          Gandhinagar      Okalipuram                       1   
97          Rajajinagar      Dayananda Nagar                  6   
98          Rajajinagar      Prakash Nagar                    4   
99          Rajajinagar      Rajaji Nagar                     5   

                                                 Venue Longitude  \
Ward number Area             Ward                                  
1           Yelahanka        Kempegowda                        5   
10          Byatarayanapura  Doddabommasandra                  4   
100         Rajajinagar      Basaveshwara Nagar               19   
101         Rajajinagar      Kamakshipalya                     2   
103         Govindarajnagara Kaveripura                        1   
...                                                          ...   
95          Gandhinagar      Subhash Nagar                    15   
96          Gandhinagar      Okalipuram                        1   
97          Rajajinagar      Dayananda Nagar                   6   
98          Rajajinagar      Prakash Nagar                     4   
99          Rajajinagar      Rajaji Nagar                      5   

                                                 Venue Category  
Ward number Area             Ward                                
1           Yelahanka        Kempegowda                       5  
10          Byatarayanapura  Doddabommasandra                 4  
100         Rajajinagar      Basaveshwara Nagar              19  
101         Rajajinagar      Kamakshipalya                    2  
103         Govindarajnagara Kaveripura                       1  
...     

In [397]:
hood_onehot = pd.get_dummies(venues[['Venue Category']], prefix="", prefix_sep="")
hood_onehot['Ward number'] = venues['Ward number']
hood_onehot['Area'] = venues['Area'] 
hood_onehot['Ward'] = venues['Ward']
fixed_columns = list(hood_onehot.columns[-3:]) + list(hood_onehot.columns[:-3])
hood_onehot = hood_onehot[fixed_columns]
hood_onehot.head()

Ward number       Area        Ward  ATM  Accessories Store  \
0           1  Yelahanka  Kempegowda    0                  0   
1           1  Yelahanka  Kempegowda    0                  0   
2           1  Yelahanka  Kempegowda    0                  0   
3           1  Yelahanka  Kempegowda    0                  0   
4           1  Yelahanka  Kempegowda    0                  0   

   American Restaurant  Andhra Restaurant  Arcade  Art Gallery  \
0                    0                  0       0            0   
1                    1                  0       0            0   
2                    0                  0       0            0   
3                    0                  0       0            0   
4                    0                  0       0            0   

   Arts & Crafts Store  ...  Tibetan Restaurant  Toy / Game Store  Trail  \
0                    0  ...                   0                 0      0   
1                    0  ...                   0                 0      0   
2                    0  ...                   0                 0      0   
3                    0  ...                   0                 0      0   
4                    0  ...                   0                 0      0   

   Train Station  Vegetarian / Vegan Restaurant  Vietnamese Restaurant  \
0              0                              0                      0   
1              0                              0                      0   
2              0                              0                      0   
3              1                              0                      0   
4              0                              0                      0   

   Vineyard  Wine Bar  Wine Shop  Women's Store  
0         0         0          0              0  
1         0         0          0              0  
2         0         0          0              0  
3         0         0          0              0  
4         0         0          0              0  

[5 rows x 173 columns]

In [467]:
preferred = {'ATM','Dog Run','Field','IT Services','Lake',"Men's Store",'Multiplex','Office', 'Park', 
          'Pharmacy','Playground','Shop & Service', 'Shopping Mall','Athletics & Sports',
          'Badminton Court','Basketball Court','Bookstore','General Entertainment','Gym',
          'Gym / Fitness Center', 'Gym Pool','Soccer Field','Convenience Store','Department Store','Farmers Market','Flea Market',
               'Grocery Store','Market','Shopping Plaza','Steakhouse','Supermarket'}


In [401]:
hood_grouped = hood_onehot.groupby(["Ward number","Area", "Ward"]).mean().reset_index()
print(hood_grouped.shape)
hood_grouped

(135, 173)


Ward number              Area                Ward  ATM  Accessories Store  \
0             1         Yelahanka          Kempegowda  0.0                0.0   
1            10   Byatarayanapura    Doddabommasandra  0.0                0.0   
2           100       Rajajinagar  Basaveshwara Nagar  0.0                0.0   
3           101       Rajajinagar       Kamakshipalya  0.5                0.0   
4           103  Govindarajnagara          Kaveripura  0.0                0.0   
..          ...               ...                 ...  ...                ...   
130          95       Gandhinagar       Subhash Nagar  0.0                0.0   
131          96       Gandhinagar          Okalipuram  0.0                0.0   
132          97       Rajajinagar     Dayananda Nagar  0.0                0.0   
133          98       Rajajinagar       Prakash Nagar  0.0                0.0   
134          99       Rajajinagar        Rajaji Nagar  0.0                0.0   

     American Restaurant  Andhra Restaurant  Arcade  Art Gallery  \
0                    0.2                0.0    0.00          0.0   
1                    0.0                0.0    0.00          0.0   
2                    0.0                0.0    0.00          0.0   
3                    0.0                0.0    0.00          0.0   
4                    0.0                0.0    0.00          0.0   
..                   ...                ...     ...          ...   
130                  0.0                0.0    0.00          0.0   
131                  0.0                0.0    0.00          0.0   
132                  0.0                0.0    0.00          0.0   
133                  0.0                0.0    0.25          0.0   
134                  0.0                0.0    0.00          0.0   

     Arts & Crafts Store  ...  Tibetan Restaurant  Toy / Game Store  Trail  \
0               0.000000  ...                 0.0               0.0    0.0   
1               0.000000  ...                 0.0               0.0    0.0   
2               0.000000  ...                 0.0               0.0    0.0   
3               0.000000  ...                 0.0               0.0    0.0   
4               0.000000  ...                 0.0               0.0    0.0   
..                   ...  ...                 ...               ...    ...   
130             0.000000  ...                 0.0               0.0    0.0   
131             0.000000  ...                 0.0               0.0    0.0   
132             0.166667  ...                 0.0               0.0    0.0   
133             0.000000  ...                 0.0               0.0    0.0   
134             0.000000  ...                 0.0               0.0    0.0   

     Train Station  Vegetarian / Vegan Restaurant  Vietnamese Restaurant  \
0              0.2                            0.0                    0.0   
1              0.0                            0.0                    0.0   
2              0.0                            0.0                    0.0   
3              0.0                            0.0                    0.0   
4              0.0                            0.0                    0.0   
..             ...                            ...                    ...   
130            0.0                            0.0                    0.0   
131            0.0                            0.0                    0.0   
132            0.0                            0.0                    0.0   
133            0.0                            0.0                    0.0   
134            0.0                            0.0                    0.0   

     Vineyard  Wine Bar  Wine Shop  Women's Store  
0         0.0       0.0        0.0            0.0  
1         0.0       0.0        0.0            0.0  
2         0.0       0.0        0.0            0.0  
3         0.0       0.0        0.0            0.0  
4         0.0       0.0        0.0            0.0  
..        ...       ...        ...            ...  


In [402]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    return row_categories_sorted.index.values[0:num_top_venues]

In [452]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
areaColumns = ['Ward number','Area', 'Ward']
freqColumns = []
for ind in np.arange(num_top_venues):
    try:
        freqColumns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        freqColumns.append('{}th Most Common Venue'.format(ind+1))
columns = areaColumns+freqColumns
# create a new dataframe
hood_venues_sorted = pd.DataFrame(columns=columns)
hood_venues_sorted['Ward number'] = hood_grouped['Ward number']
hood_venues_sorted['Area'] = hood_grouped['Area']
hood_venues_sorted['Ward'] = hood_grouped['Ward']
for ind in np.arange(hood_grouped.shape[0]):
    row_categories = hood_grouped.iloc[ind, :].iloc[3:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    hood_venues_sorted.iloc[ind, 3:] = row_categories_sorted.index.values[0:num_top_venues]

hood_venues_sorted.head()

Ward number              Area                Ward 1st Most Common Venue  \
0           1         Yelahanka          Kempegowda            Smoke Shop   
1          10   Byatarayanapura    Doddabommasandra                  Lake   
2         100       Rajajinagar  Basaveshwara Nagar  Fast Food Restaurant   
3         101       Rajajinagar       Kamakshipalya                   ATM   
4         103  Govindarajnagara          Kaveripura                  Park   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0   American Restaurant        Ice Cream Shop         Train Station   
1     Indian Restaurant           Supermarket           Snack Place   
2        Ice Cream Shop     Indian Restaurant                Market   
3           Bus Station     Fish & Chips Shop                 Field   
4         Women's Store               Dog Run     Fish & Chips Shop   

  5th Most Common Venue        6th Most Common Venue 7th Most Common Venue  \
0                  Café                      Dog Run     Fish & Chips Shop   
1         Women's Store  Eastern European Restaurant     Fish & Chips Shop   
2           Snack Place                   Playground      Asian Restaurant   
3  Fast Food Restaurant               Farmers Market           Event Space   
4                 Field         Fast Food Restaurant        Farmers Market   

  8th Most Common Venue        9th Most Common Venue  \
0                 Field         Fast Food Restaurant   
1                 Field         Fast Food Restaurant   
2          Burger Joint         Karnataka Restaurant   
3     Electronics Store  Eastern European Restaurant   
4           Event Space            Electronics Store   

        10th Most Common Venue  
0               Farmers Market  
1               Farmers Market  
2                    Gastropub  
3                   Donut Shop  
4  Eastern European Restaurant

In [453]:
kclusters = 5
hood_grouped_clustering = hood_grouped.drop(["Ward number","Area","Ward"], 1)
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(hood_grouped_clustering)
kmeans.labels_[0:10]

array([3, 0, 3, 2, 3, 0, 0, 3, 3, 3])

In [454]:
hood_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
hood_venues_sorted.head()
hood_merged = hood
hood_merged = hood_merged.join(hood_venues_sorted.drop(['Area','Ward'],1)
                                     .set_index('Ward number'), on='Ward number')
hood_merged['Cluster Labels'].fillna(hood_merged['Cluster Labels'].mode()[0], inplace=True)

In [455]:
print(hood_merged.shape)
hood_merged['Cluster Labels'] = hood_merged['Cluster Labels'].astype(int)
hood_merged.head()

(141, 16)


Ward number             Area                      Ward Latitude Longitude  \
0           1        Yelahanka                Kempegowda  13.0993   77.5926   
1           2        Yelahanka              Chowdeshwari  13.1081   77.5937   
2           4        Yelahanka  Yelahanka Satellite Town   13.097   77.5841   
3           5  Byatarayanapura                    Jakkur  12.9519   77.5445   
4          10  Byatarayanapura          Doddabommasandra  13.0625   77.5591   

   Cluster Labels    1st Most Common Venue 2nd Most Common Venue  \
0               3               Smoke Shop   American Restaurant   
1               3         Business Service         Women's Store   
2               3  South Indian Restaurant                Bakery   
3               0        Indian Restaurant           Bus Station   
4               0                     Lake     Indian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Ice Cream Shop         Train Station                  Café   
1               Dog Run     Fish & Chips Shop                 Field   
2   American Restaurant          Dessert Shop                   Gym   
3      Department Store         Women's Store     Fish & Chips Shop   
4           Supermarket           Snack Place         Women's Store   

         6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                      Dog Run     Fish & Chips Shop                 Field   
1         Fast Food Restaurant        Farmers Market           Event Space   
2                   Restaurant     Fish & Chips Shop                 Field   
3                        Field  Fast Food Restaurant        Farmers Market   
4  Eastern European Restaurant     Fish & Chips Shop                 Field   

  9th Most Common Venue       10th Most Common Venue  
0  Fast Food Restaurant               Farmers Market  
1     Electronics Store  Eastern European Restaurant  
2  Fast Food Restaurant               Farmers Market  
3           Event Space            Electronics Store  
4  Fast Food Restaurant               Farmers Market

In [422]:
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

In [449]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
print(rainbow)


markers_colors = []
for lat, lon, poi, cluster in zip(hood_merged['Latitude'], hood_merged['Longitude'], 
                                  hood_merged['Ward'], hood_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
    
legend_html =   '''
                <div style="position: fixed; 
                            bottom: 50px; left: 50px; width: 100px; height: 120px; 
                            border:2px solid grey; z-index:9999; font-size:8px;
                            ">&nbsp; <b>Cool Legend </b>
                              <br>&nbsp;&nbsp;&nbsp;&nbsp; Cluster 0 &nbsp; &nbsp;&nbsp; &nbsp;<i class="fa fa-square fa-2x" style="color:#ff0000"></i>
                              <br>&nbsp;&nbsp;&nbsp;&nbsp; Cluster 2 &nbsp; &nbsp;&nbsp;&nbsp; <i class="fa fa-square fa-2x" style="color:#8000ff"></i>
                              <br>&nbsp;&nbsp;&nbsp;&nbsp; Cluster 3 &nbsp; &nbsp;&nbsp;&nbsp; <i class="fa fa-square fa-2x" style="color:#00b5eb"></i>
                              <br>&nbsp;&nbsp;&nbsp;&nbsp; Cluster 4 &nbsp; &nbsp;&nbsp;&nbsp; <i class="fa fa-square fa-2x" style="color:#80ffb4"></i>
                              <br>&nbsp;&nbsp;&nbsp;&nbsp; Cluster 5 &nbsp; &nbsp;&nbsp;&nbsp; <i class="fa fa-square fa-2x" style="color:#ffb360"></i>
                </div>
                ''' 

map_clusters.get_root().html.add_child(folium.Element(legend_html))
map_clusters

['#8000ff', '#00b5eb', '#80ffb4', '#ffb360', '#ff0000']


In [470]:
score = []
for i in hood_merged.index:
    score.append(len(list(set(hood_merged.iloc[i][6:]) & preferred)))
hood_merged['Total'] = score
hood_merged.head()

Ward number             Area                      Ward Latitude Longitude  \
0           1        Yelahanka                Kempegowda  13.0993   77.5926   
1           2        Yelahanka              Chowdeshwari  13.1081   77.5937   
2           4        Yelahanka  Yelahanka Satellite Town   13.097   77.5841   
3           5  Byatarayanapura                    Jakkur  12.9519   77.5445   
4          10  Byatarayanapura          Doddabommasandra  13.0625   77.5591   

   Cluster Labels    1st Most Common Venue 2nd Most Common Venue  \
0               3               Smoke Shop   American Restaurant   
1               3         Business Service         Women's Store   
2               3  South Indian Restaurant                Bakery   
3               0        Indian Restaurant           Bus Station   
4               0                     Lake     Indian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Ice Cream Shop         Train Station                  Café   
1               Dog Run     Fish & Chips Shop                 Field   
2   American Restaurant          Dessert Shop                   Gym   
3      Department Store         Women's Store     Fish & Chips Shop   
4           Supermarket           Snack Place         Women's Store   

         6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                      Dog Run     Fish & Chips Shop                 Field   
1         Fast Food Restaurant        Farmers Market           Event Space   
2                   Restaurant     Fish & Chips Shop                 Field   
3                        Field  Fast Food Restaurant        Farmers Market   
4  Eastern European Restaurant     Fish & Chips Shop                 Field   

  9th Most Common Venue       10th Most Common Venue  Total  
0  Fast Food Restaurant               Farmers Market      3  
1     Electronics Store  Eastern European Restaurant      3  
2  Fast Food Restaurant               Farmers Market      3  
3           Event Space            Electronics Store      3  
4  Fast Food Restaurant               Farmers Market      4

In [477]:
beng_map = folium.Map(location=[latitude, longitude],zoom_start=11)

fs = plugins.Fullscreen()
beng_map.add_child(fs)

folium.GeoJson('BBMP.GeoJSON').add_to(beng_map)

beng_map

In [491]:

#!pip install geojson
import geojson
with open('BBMP.GeoJSON') as f:
    gj = geojson.load(f)
features = gj['features'][0]
print(features)

# create a plain world map
beng_map = folium.Map(location=[latitude, longitude], zoom_start=2, tiles='Mapbox Bright')

# folium.Choropleth(
#     geo_data='buurten.geojson.json',
#     name='Distance to Prinsejagt',
#     data=df_ehv_clusters,
#     columns=['Buurtcode', 'd_prinsejagt'],
#     key_on='feature.properties.buurtcode',
#     fill_color='YlGn',
#     fill_opacity=0.7,
#     line_opacity=0.2,
#     legend_name='Distance to Prinsejagt'
# ).add_to(prinsejagt_map)

# generate choropleth map using the total immigration of each country to Canada from 1980 to 2013
beng_map.choropleth(
    geo_data=beng_geo,
    data=hood_merged,
    columns=['Ward', 'Total'],
    key_on='feature.properties.WARD_NO',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Immigration to Canada'
)

# display map
beng_map

{"geometry": {"coordinates": [[[[77.592294, 13.097196], [77.590945, 13.098422], [77.58908, 13.100057], [77.587331, 13.101375], [77.58712, 13.101557], [77.586904, 13.101727], [77.586514, 13.102033], [77.585911, 13.102505], [77.585065, 13.103173], [77.584105, 13.104024], [77.583197, 13.1049], [77.582526, 13.105613], [77.581835, 13.10642], [77.581297, 13.107069], [77.581082, 13.107362], [77.580989, 13.107561], [77.580686, 13.107877], [77.580023, 13.108276], [77.579245, 13.108733], [77.578716, 13.109149], [77.578021, 13.108352], [77.577304, 13.107331], [77.577297, 13.107305], [77.576726, 13.107552], [77.57625, 13.107727], [77.575729, 13.107839], [77.575035, 13.107952], [77.574061, 13.108345], [77.57352, 13.108521], [77.57326, 13.107928], [77.572677, 13.108107], [77.572257, 13.108055], [77.572349, 13.109587], [77.572638, 13.111641], [77.572711, 13.113154], [77.572592, 13.114633], [77.572178, 13.116936], [77.572199, 13.118974], [77.572021, 13.120229], [77.572022, 13.122136], [77.571769, 13.1